In [13]:
import gspread
import pandas as pd
from oauth2client.service_account import ServiceAccountCredentials
import re

from pydrive.auth import GoogleAuth
from pydrive.drive import GoogleDrive

# Konfigurasi autentikasi dengan service account
gauth = GoogleAuth()
gauth.auth_method = 'service'
gauth.credentials = ServiceAccountCredentials.from_json_keyfile_name(
    "D:/House of Om/API/spreadsheet-439003-68ab13b2ce0d.json",  # Update dengan path file service account Anda
    scopes=['https://www.googleapis.com/auth/drive']
)

In [14]:
drive = GoogleDrive(gauth)
file_id = "1TjAk0eGWv7AhsoTqWsL6Wn7UR5p3mvGa"
downloaded = drive.CreateFile({'id': file_id})
downloaded.GetContentFile(r"data/offline_sales.xlsx")  # Simpan sebagai file lokal

download_monthly = pd.read_excel(r"data/offline_sales.xlsx",
                                 sheet_name="MONTHLY (2025)")
download_monthly.to_excel(r"data/offline_sales.xlsx", index=False)

In [15]:
offline_sales = pd.read_excel(r"data/offline_sales.xlsx")

# Ensure 'DATE OF PAYMENT' is in datetime format
offline_sales['DATE OF PAYMENT'] = pd.to_datetime(offline_sales['DATE OF PAYMENT'], errors='coerce')

# Extract month names from 'DATE OF PAYMENT' and convert to uppercase
offline_sales['MONTH'] = offline_sales['DATE OF PAYMENT'].dt.strftime('%B').str.upper()

# Reorder 'MONTH' column to be next to the first column
cols = list(offline_sales.columns)
month_index = cols.index('MONTH')
cols.insert(1, cols.pop(month_index))
offline_sales = offline_sales[cols]

In [16]:
months = [
    "JANUARY", "FEBRUARY", "MARCH", "APRIL", "MAY", "JUNE",
    "JULY", "AUGUST", "SEPTEMBER", "OCTOBER", "NOVEMBER", "DECEMBER"
]

offline_sales['MONTH'] = None  # Inisialisasi kolom MONTH

# Gunakan .astype(str) untuk mengonversi ke string
month_indices = offline_sales[offline_sales.iloc[:, 0].astype(str).str.strip().str.upper().isin(months)].index

offline_sales.loc[month_indices, 'MONTH'] = offline_sales.iloc[month_indices, 0].astype(str).str.strip().str.upper()
offline_sales['MONTH'] = offline_sales['MONTH'].fillna(method='ffill')  # Isi nilai bulan ke bawah

# Hapus baris yang berisi nama bulan
offline_sales = offline_sales[~offline_sales.index.isin(month_indices)]

# Pindahkan kolom MONTH ke posisi kedua
cols = list(offline_sales.columns)
month_index = cols.index('MONTH')
cols.insert(1, cols.pop(month_index))
offline_sales = offline_sales[cols]

C:\Users\user\AppData\Local\Temp\ipykernel_17580\2639417849.py:12: FutureWarning: Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  offline_sales['MONTH'] = offline_sales['MONTH'].fillna(method='ffill')  # Isi nilai bulan ke bawah


In [17]:
# Ensuring consistent NaN representation in relevant columns
offline_sales['NO'] = offline_sales['NO'].replace('', pd.NA)
offline_sales['PAYMENT GATEWAY'] = offline_sales['PAYMENT GATEWAY'].replace('', pd.NA)

# Menghapus baris di mana kolom 'MONTH' memiliki nilai, 
# tetapi kolom 'NO' di sebelah kiri dan kolom 'PAYMENT GATEWAY' di sebelah kanan kosong
offline_sales = offline_sales[~((offline_sales['MONTH'].notnull()) &
                                (offline_sales['NO'].isnull()) &
                                (offline_sales['PAYMENT GATEWAY'].isnull()))].reset_index(drop=True)

# Menghapus baris yang seluruhnya kosong (semua kolom bernilai NaN)
offline_sales = offline_sales.dropna(how='all').reset_index(drop=True)

# Menghapus baris di mana 'TRANSACTION ID', 'DATE OF PAYMENT', dan 'NAME' kosong
offline_sales = offline_sales[~(
                offline_sales['TRANSACTION ID'].isnull() &
                offline_sales['DATE OF PAYMENT'].isnull() &
                offline_sales['NAME'].isnull()
)].reset_index(drop=True)

offline_sales['NO'] = range(1, len(offline_sales) + 1)

# Tampilkan hasil setelah logika diperbaiki dan diterapkan
offline_sales

NO    MONTH PAYMENT GATEWAY  \
0        1  JANUARY          XENDIT   
1        2  JANUARY          XENDIT   
2        3  JANUARY          XENDIT   
3        4  JANUARY          XENDIT   
4        5  JANUARY          XENDIT   
...    ...      ...             ...   
2672  2673    APRIL          XENDIT   
2673  2674    APRIL          XENDIT   
2674  2675    APRIL          XENDIT   
2675  2676    APRIL          XENDIT   
2676  2677    APRIL          STRIPE   

                                         TRANSACTION ID DATE OF PAYMENT  \
0            CS-Celestial-Renewal-Deposit-1735663477779      2025-01-01   
1                                         INV6498867006      2025-01-01   
2                                         INV7204857432      2025-01-01   
3                                         INV5648269840      2025-01-01   
4                                         INV2078740359      2025-01-01   
...                                                 ...             ...   
2672  CS-ptaumb-fd488704aeb14eb7-9c18d1bec89d457e-17...      2025-04-29   
2673                                      INV9810726322      2025-04-29   
2674  ptaumb-48ec1ab8eef646f2-9fe7b6d0de9e9196-17459...      2025-04-29   
2675  ptaumb-c945dc903e82471f-aae5cf651e6f4204-17459...      2025-04-29   
2676                        pi_3RJ8I1E9dkCSzeZN1aGIgPK3      2025-04-29   

      PRODUCT PRICE (USD) AMOUNT PAID (IDR)  AMOUNT PAID (USD)  \
0                  2470.0           6674400              400.0   
1                  2135.0           6674400              400.0   
2                  1590.0          26530740             1590.0   
3                  1855.0           6674400              400.0   
4                  3385.0          56440395             3385.0   
...                   ...               ...                ...   
2672               2870.0          41496000             2470.0   
2673               2065.0          34692000             2065.0   
2674               3295.0          39600000             2400.0   
2675               3295.0           8266500              495.0   
2676               2625.0               NaN             2625.0   

      AMOUNT PAID (EUR)                  NAME                         EMAIL  \
0                   NaN          KACEY MILLER     KACEYMILLER7777@GMAIL.COM   
1                   NaN          ALMASS BADAT        ALMASS@ALMASSBADAT.COM   
2                   NaN          TSZ WAI PONG          PONGTSZWAI@GMAIL.COM   
3                   NaN           KATIE COHEN            KATII289@GMAIL.COM   
4                   NaN          LINGHUI ZHAO       ZZZHAOLINGHUI@GMAIL.COM   
...                 ...                   ...                           ...   
2672                NaN  Beverly Dazo Refundo             bamdazo@yahoo.com   
2673                NaN         Farah Capsari        casparifarah@gmail.com   
2674                NaN        Narmin Aliyeva  narmin.aliyeva1990@gmail.com   
2675                NaN        Narmin Aliyeva  narmin.aliyeva1990@gmail.com   
2676                NaN          Kyle Trainor                           NaN   

          COURSE SCHEDULE   PRODUCT TYPE        LOCATION      PAYMENT NOTES  \
0     2025-01-13 00:00:00     200HR-TWIN     The Mansion            Deposit   
1     2025-04-07 00:00:00     200HR-TWIN          Pelaga            Deposit   
2     2025-06-30 00:00:00     200HR-DORM  Melati Cottage       Full Payment   
3     2025-04-07 00:00:00   200HR-TRIPLE   Yoga Amertham            Deposit   
4     2025-05-05 00:00:00    200HR-VILLA          Pelaga       Full Payment   
...                   ...            ...             ...                ...   
2672  2025-06-23 00:00:00  200HR-PRIVATE     The Mansion       Full Payment   
2673  2025-05-05 00:00:00     200HR-TWIN          Pelaga       Full Payment   
2674  2025-05-12 00:00:00     200HR-TWIN     The Mansion  Remaining Payment   
2675  2025-05-12 00:00:00     200HR-TWIN     The Mansion  Remaining Payment   
2676                  NaN  

In [18]:
import pandas as pd
import numpy as np
from difflib import get_close_matches
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report

def auto_correct_scheduled_month(date_value):
    if pd.isnull(date_value):
        return np.nan  # Leave blank if already empty

    # Check if value is already a datetime object
    if isinstance(date_value, pd.Timestamp):
        return date_value.strftime('%d-%b-%Y')  # Convert to standard format

    # Dictionary of valid months
    valid_months = {
        "Jan": "Jan", "Feb": "Feb", "Mar": "Mar", "Apr": "Apr",
        "May": "May", "Jun": "Jun", "Jul": "Jul", "Aug": "Aug",
        "Sep": "Sep", "Oct": "Oct", "Nov": "Nov", "Dec": "Dec"
    }

    try:
        # Try parsing the date as it is
        parsed_date = pd.to_datetime(str(date_value), errors='coerce')
        if not pd.isnull(parsed_date):
            return parsed_date.strftime('%d-%b-%Y')  # Standardize format
    except ValueError:
        pass

    # Attempt correction for non-standard strings
    parts = str(date_value).split()
    if len(parts) == 3:
        day, month, year = parts
        corrected_month = get_close_matches(month.title(), valid_months.keys(), n=1)
        if corrected_month:
            month = corrected_month[0]
        if len(year) == 2:  # Handle two-digit year
            year = f"20{year}" if int(year) < 50 else f"19{year}"
        elif len(year) == 3:  # Handle three-digit year
            year = f"20{year}"

        corrected_date = f"{day}-{month}-{year}"
        try:
            parsed_date = pd.to_datetime(corrected_date, format='%d-%b-%Y', errors='coerce')
            if not pd.isnull(parsed_date):
                return parsed_date.strftime('%d-%b-%Y')
        except ValueError:
            pass

    # If parsing/correction fails, return blank
    return np.nan

# Apply the auto-correction logic to the `SCHEDULED MONTH` column
offline_sales['corrected_schedule_month'] = offline_sales['COURSE SCHEDULE'].apply(auto_correct_scheduled_month)

# Display the results for validation
processed_scheduled_month = offline_sales[['COURSE SCHEDULE', 'corrected_schedule_month']].copy()

In [19]:
# Create a new column 'WEEK' that maps the week number of each date in the month
offline_sales['WEEK'] = pd.to_datetime(offline_sales['DATE OF PAYMENT'], errors='coerce').apply(
    lambda x: f"WEEK {((x.day - 1) // 7) + 1}" if pd.notnull(x) else None
)

In [20]:
# Create a 'PERIOD' column that specifies the range of dates for each week
def week_period(date):
    if pd.notnull(date):
        start_of_week = (date.day - 1) // 7 * 7 + 1
        end_of_week = min(start_of_week + 6, pd.Timestamp(date.year, date.month, 1).days_in_month)
        return f"{pd.Timestamp(date.year, date.month, start_of_week).date()} - {pd.Timestamp(date.year, date.month, end_of_week).date()}"
    return None

offline_sales['PERIOD'] = pd.to_datetime(offline_sales['DATE OF PAYMENT'], errors='coerce').apply(week_period)
offline_sales['PERIOD'] = offline_sales['PERIOD'].str.replace(' - ', ' to ')

In [21]:
# Extract the year from 'DATE OF PAYMENT' and add it as a new column 'YEAR'
offline_sales['YEAR'] = pd.to_datetime(offline_sales['DATE OF PAYMENT'], errors='coerce').dt.year

# Pastikan nilai NaN tetap kosong dan ubah tipe kolom ke Int64 (nullable integer)
offline_sales['YEAR'] = offline_sales['YEAR'].astype('Int64')

# Reorder columns to place 'YEAR' next to 'MONTH'
columns = list(offline_sales.columns)
month_index = columns.index('MONTH')
columns.insert(month_index + 1, columns.pop(columns.index('YEAR')))
offline_sales = offline_sales[columns]

In [22]:
# Daftar kolom yang ingin diperiksa
columns_to_check = ['PAYMENT GATEWAY', 'TRANSACTION ID', 'PRODUCT PRICE (USD)', 'AMOUNT PAID (IDR)', 'AMOUNT PAID (USD)']

# Hapus baris di mana semua kolom dalam 'columns_to_check' adalah NaN
offline_sales = offline_sales.dropna(subset=columns_to_check, how='all')

In [23]:
# Filter: Hanya baris dengan kolom 'NOTES' yang memiliki nilai sesuai daftar tertentu
allowed_notes = ["Full Payment"
                     ,"Deposit"
                     ,"Split Full Payment"
                     ,"Remaining Payment"
                     ]
offline_sales = offline_sales[
    offline_sales['PAYMENT NOTES'].str.strip().isin(allowed_notes)
]

In [24]:
offline_sales.to_excel(r"data/offline_sales.xlsx", index=False)